In [ ]:
import dask
from IPython.display import clear_output
import math
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from sklearn.linear_model import QuantileRegressor
from sklearn.metrics import r2_score, mean_squared_error
import warnings
warnings.filterwarnings('ignore')
import xarray as xr

# LOADING DATASETS
### Please unzip all files before running the code !

In [ ]:
# LOADING MRR DATA (may take a while)
with dask.config.set(**{'array.slicing.split_large_chunks': False}):
    ds_mrr = xr.open_mfdataset("MRR_DDU_1min_*.nc")
    
time_mrr = pd.to_datetime(ds_mrr["time"])
Ze_mrr = ds_mrr["Ze"].where(ds_mrr["quality"]<60000.).where(ds_mrr["Ze"]>-5.)
# bad quality data and equivalent reflectivity lower than -5 dBz are discarded
offset = 6.14
# offset due to the radome attenuation (see Grazioli et al 2017a)
Ze_mrr = 10.**((Ze_mrr+offset)/10.).values
# conversion in linear units

In [ ]:
# LOADING PLUVIOMETER (=snow-gauge) DATA
ds_pl = xr.open_dataset("Pluvio_DDU_1min_2015-2023.nc")
time_pl = pd.to_datetime(ds_pl["time"])
Bucket = ds_pl["Bucket"]

In [ ]:
# LOADING METEOFRANCE OBSERVATIONS DATA (for filtering)
ds_mto = xr.open_dataset("MTO_DDU_1hr_2015-2023.nc")
time_mto = pd.to_datetime(ds_mto['time'])
F_mto = ds_mto["F"] # hourly wind speed

### Ze-S relation computation

In [ ]:
# A small useful function
def find_start(timevec, start) :
    # time vector (datetimes array), start time (str)
    idx = (np.nanargmin(abs(timevec - pd.to_datetime(start))))
    return idx

In [ ]:
### User parameters ###
start = "2015-11-23"
end = "2023-07-01"
integration_time = 60 # in minutes
remove_year = 0
#######################

timevec = pd.date_range(pd.to_datetime(start), pd.to_datetime(end), freq=str(integration_time)+'T') ; nt = len(timevec)

past_mrr = find_start(time_mrr,start) # finding the first index
past_pl = find_start(time_pl,start)

ahead_mrr = integration_time + 1 # we scan the vector [integration time + 1] minutes ahead, see below
ahead_pl = ahead_mrr # same
# if the integration time is < 60 minutes, we make a linear interpolation of the Météo-France hourly wind
if integration_time < 60 :
    F = F_mto.resample(time=str(integration_time)+'T').interpolate("linear")
    ahead_mto = int(60./integration_time) + 1
else :
    F = F_mto
    ahead_mto = math.ceil(integration_time/60.) + 1
time_mto = pd.to_datetime(F.time)
past_mto = find_start(time_mto,start)

    
x = [] ; y = [] # vectors that will be filled with filtered data points

for l in range(nt-1) :
    
    # Select data for each timestep. 
    # We do not scan all the dataset, only a small part between the past and past+ahead indexes, 
    # in order to reduce the computation time. 
    mask_mrr = [idx for idx,ti in enumerate(time_mrr[past_mrr:past_mrr+ahead_mrr]) if timevec[l] < ti <= timevec[l+1]]
    mask_pl = [idx for idx,ti in enumerate(time_pl[past_pl:past_pl+ahead_pl]) if timevec[l] < ti <= timevec[l+1]]
    mask_mto = [idx for idx,ti in enumerate(time_mto[past_mto:past_mto+ahead_mto]) if timevec[l] < ti <= timevec[l+1]]

    # if both dataset have data, and if we do not remove the current year for sensibility studies
    if len(mask_pl) and len(mask_mrr) and not timevec[l].year == remove_year :
        Zei = np.nanmedian(Ze_mrr[past_mrr:past_mrr+ahead_mrr,2][mask_mrr])
        Si = (Bucket[past_pl:past_pl+ahead_pl][mask_pl].diff("time").sum().values) * float(60./integration_time)
        # beware of the conversion to mm/hr in case the integration time is not 60 minutes
        Fi = np.nanmedian(F[past_mto:past_mto+ahead_mto][mask_mto])
        
        # Filtering steps 
        filter1 = Fi > 7. or np.isnan(Fi)
        filter2 = (Si < 0.1 or Si > 12.)
        
        if not (filter1 or filter2) and (Si > 0 and Zei > 0) :
            x.append(Si)
            y.append(Zei)
            
    past_mrr += len(mask_mrr) # progression in the 1-min vector
    past_pl += len(mask_pl)
    past_mto += len(mask_mto)
            
            
    if not l%int(nt/100.) :
        clear_output()
        print("Prog.: %.2g%%, len(mask_mrr) = %d, len(mask_pl) = %d, len(mask_mto) = %d"\
              %(float(l)/float(nt)*100.,len(mask_mrr),len(mask_pl),len(mask_mto)))
clear_output()
print("Remaining data points : %d" %(len(x)))

In [ ]:
# Computation in log space using a quantile linear regression
quantilereg = QuantileRegressor(quantile=0.5,solver='highs',alpha=0).fit(np.log(x).reshape(-1, 1), np.log(y))
A = quantilereg.coef_ ; B = quantilereg.intercept_
a = np.exp(B) ; b = float(A)
print('This study : a=%3.3g'%(a),'b=%3.3g'%(b),'N=',len(x),"R²=%.3g"%(r2_score(np.log(y),A*np.log(x)+B)))
RMSE_quantile = mean_squared_error(np.log(y),A*np.log(x)+B, squared=False)
print('Uncertainty (RMSE in log space) : %.3g' %(RMSE_quantile))

# Relations from other studies
Agrazioli = 0.91 ; Bgrazioli = np.log(76.)
print("R² for Grazioli=",r2_score(np.log(y),Agrazioli*np.log(x)+Bgrazioli))
Ascarchilli = 1.15 ; Bscarchilli = np.log(54.)
print("R² for Scarchilli=",r2_score(np.log(y),Ascarchilli*np.log(x)+Bscarchilli))
Asouverijns = 1.10 ; Bsouverijns = np.log(18.)
print("R² for Souverijns=",r2_score(np.log(y),Asouverijns*np.log(x)+Bsouverijns))

xplot = np.linspace(0.01,np.exp(1),100) ; xplot = np.log(xplot)

fig,ax = plt.subplots(dpi=300)
ax.grid()
ax.set_xlabel("ln(S)")
ax.set_ylabel("ln(Ze)")
ax.set_xlim(-2.5,1)
ax.set_ylim(0,5.5)
ax.plot(xplot, A*xplot+B,color='blue',label='This study',linewidth=1.5)
ax.plot(np.log(x),np.log(y),'+',color='black')
ax.fill_between(xplot, y1=A*xplot+B-RMSE_quantile,y2=A*xplot+B+RMSE_quantile,color='blue',alpha=0.3)
ax.plot(xplot, Agrazioli*xplot+Bgrazioli,color='red',linestyle='dashdot',label='Grazioli et al. (2017a)')
ax.plot(xplot,Ascarchilli*xplot+Bscarchilli,color='gold',linestyle='dashed',label='Scarchilli et al. (2020)')
ax.plot(xplot,Asouverijns*xplot+Bsouverijns,color='magenta',linestyle='dotted',label='Souverijns et al. (2017)',linewidth=1.75)

ax.legend(fontsize=9)
